In [1]:
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation as LDA

In [2]:
%matplotlib inline

In [3]:
n_terms = 4000
n_topics = 80
max_iter = 5

# Prepare Data

In [4]:
import os

In [7]:
os.system("cat ./corpus/cord19_* > ./corpus/corpus.csv")

0

In [8]:
corpus = pd.read_csv('corpus/corpus.csv', sep='|')

In [9]:
corpus.head()

doc_key  \
0  c630ebcdf30652f0422c3ec12a00b50241dc9bd9   
1  53eccda7977a31e3d0f565c884da036b1e85438e   
2  210a892deb1c61577f6fba58505fd65356ce6636   
3  e3b40cc8e0e137c416b4a2273a4dca94ae8178cc   
4  0df0d5270a9399cf4e23c0cdd877a80616a9725e   

                                           doc_title  \
0  Angiotensin-converting enzyme 2 (ACE2) as a SA...   
1  Comparative genetic analysis of the novel coro...   
2  Incubation Period and Other Epidemiological Ch...   
3  Characteristics of and Public Health Responses...   
4  An updated estimation of the risk of transmiss...   

                                         doc_url  \
0  https://dx.doi.org/10.1007/s00134-020-05985-9   
1   https://dx.doi.org/10.1038/s41421-020-0147-1   
2          https://dx.doi.org/10.3390/jcm9020538   
3          https://dx.doi.org/10.3390/jcm9020575   
4   https://dx.doi.org/10.1016/j.idm.2020.02.001   

                                         doc_content doc_label  
0  SARS-CoV-2 has been sequenced [3] . A phylogen...       CZI  
1  Comparative genetic analysis of the novel coro...       CZI  
2  As of 31 January 2020, mainland China reported...       CZI  
3  In December 2019, a cluster of pneumonia of un...       CZI  
4  Coronaviruses are a group of enveloped viruses...       CZI

## Create Vector Space

We use Scikit Learn's CountVectorizer to convert our F1 corpus of paragraphs into a document-term vector space of word counts.

In [10]:
tfv = CountVectorizer(max_features=n_terms, stop_words='english')
tf = tfv.fit_transform(corpus.doc_content)
TERMS = tfv.get_feature_names()

# Generate Model

We run Scikit Learn's [LatentDirichletAllocation algorithm](https://scikit-learn.org/stable/modules/generated/sklearn.decomposition.LatentDirichletAllocation.html#sklearn.decomposition.LatentDirichletAllocation) and extract the THETA and PHI tables.

In [11]:
lda = LDA(n_components=n_topics, max_iter=max_iter, learning_offset=50., random_state=0)

In [ ]:
tmodel = lda.fit_transform(tf)

## THETA

In [ ]:
THETA = pd.DataFrame(tmodel)
THETA.columns.name = 'topic_id'

## PHI

In [ ]:
PHI = pd.DataFrame(lda.components_, columns=TERMS)
PHI.index.name = 'topic_id'
PHI.columns.name  = 'term_str'

# Inspect Results

## Get Top Terms per Topic

In [ ]:
TOPICS = PHI.stack().to_frame().rename(columns={0:'weight'})\
    .groupby('topic_id')\
    .apply(lambda x: 
           x.weight.sort_values(ascending=False)\
               .head(10)\
               .reset_index()\
               .drop('topic_id',1)\
               .term_str)

In [ ]:
TOPICS['label'] = TOPICS.apply(lambda x: str(x.name) + ' ' + ' '.join(x), 1)

## Sort Topics by Doc Weight

In [ ]:
TOPICS['doc_weight_sum'] = THETA.sum()

In [ ]:
TOPICS.sort_values('doc_weight_sum', ascending=True).plot.barh(y='doc_weight_sum', x='label', figsize=(5,20)) 

# Clutser Topics

In [ ]:
import scipy.cluster.hierarchy as sch
from scipy.spatial.distance import pdist
from sklearn.cluster import AgglomerativeClustering
from sklearn.preprocessing import normalize
import matplotlib.pyplot as plt

In [ ]:
def plot_tree(tree, labels):
    plt.figure()
    fig, axes = plt.subplots(figsize=(5, 20))
    dendrogram = sch.dendrogram(tree, labels=labels, orientation="left")
    plt.tick_params(axis='both', which='major', labelsize=14)

In [ ]:
SIMS = pdist(normalize(PHI), metric='cosine')
TREE = sch.linkage(SIMS, method='ward')

In [ ]:
labels = TOPICS.label.tolist() #["{}: {}".format(a,b) for a, b in zip(AUTHORS.index,  AUTHORS.topterms.tolist())]

In [ ]:
# labels

In [ ]:
plot_tree(TREE, labels)

# LDA Viz

In [52]:
import pyLDAvis
import pyLDAvis.sklearn
pyLDAvis.enable_notebook()

In [53]:
pyLDAvis.sklearn.prepare(lda, tf, tfv)

/Users/rca2t/anaconda3/envs/DS5001/lib/python3.5/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
79     3.260558        1       1 -0.162646  0.068980
30     3.074120        1       2 -0.195925  0.016948
42     2.789597        1       3  0.150716  0.017233
70     2.733598        1       4 -0.148346 -0.062336
48     2.362960        1       5  0.183866  0.057501
47     2.162248        1       6  0.090627 -0.058746
37     2.095379        1       7 -0.157465  0.034943
55     2.095225        1       8 -0.141174 -0.123970
45     2.084618        1       9  0.064628  0.133957
15     2.025293        1      10 -0.153936 -0.057626
22     1.927520        1      11  0.068063 -0.112719
65     1.894061        1      12 -0.180407 -0.056719
69     1.883981        1      13 -0.062675  0.128831
74     1.831576        1      14  0.101255 -0.148908
38     1.829554        1      15 -0.004017  0.100870
14     1.815218        1      16  0.205983 -0.028347
36     1.815188        1      17  0.154176 -0.017665
43     1.811683        1      18 -0.031786  0.213121
52     1.786470        1      19 -0.029772  0.023860
61     1.776137        1      20  0.062280  0.109820
73     1.730088        1      21 -0.004702  0.120197
40     1.724417        1      22  0.121129 -0.052844
57     1.707659        1      23 -0.216472 -0.008852
62     1.703016        1      24  0.079592 -0.067838
51     1.699666        1      25  0.072984 -0.007124
39     1.697736        1      26  0.005825  0.023752
46     1.685799        1      27  0.175113 -0.026299
6      1.671708        1      28  0.106822 -0.112281
76     1.591048        1      29 -0.200242 -0.020481
50     1.520450        1      30  0.003222  0.129629
...         ...      ...     ...       ...       ...
5      0.973177        1      51 -0.150782 -0.053534
12     0.958497        1      52 -0.052864 -0.043958
66     0.927054        1      53 -0.152454 -0.065715
54     0.898065        1      54 -0.078860 -0.019002
44     0.841191        1      55  0.020807  0.079117
71     0.800893        1      56  0.152893 -0.097670
34     0.751283        1      57 -0.166828  0.009301
7      0.728020        1      58  0.059643 -0.146210
19     0.703860        1      59  0.122471  0.081144
58     0.649761        1      60 -0.031701  0.135223
64     0.637044        1      61  0.043089  0.051904
27     0.560639        1      62 -0.068097 -0.081908
26     0.529516        1      63 -0.065864 -0.060992
2      0.498140        1      64 -0.019686 -0.106539
29     0.465098        1      65 -0.088757  0.114974
67     0.449323        1      66  0.131796  0.026706
33     0.386986        1      67  0.045921 -0.021987
23     0.370031        1      68  0.060937  0.000146
25     0.353157        1      69 -0.076155 -0.034283
4      0.343243        1      70  0.098119  0.092049
21     0.336948        1      71  0.155550  0.065757
17     0.334221        1      72  0.125370 -0.054481
32     0.327002        1      73 -0.101063  0.065574
0      0.315123        1      74  0.061528 -0.056357
24     0.306432        1      75  0.066086 -0.053788
10     0.298995        1      76 -0.127167 -0.039220
77     0.259912        1      77  0.020015 -0.016117
78     0.238584        1      78 -0.127783  0.022968
35     0.181570        1      79 -0.031393 -0.053364
49     0.104645        1      80 -0.065723  0.080753

[80 rows x 5 columns], topic_info=     Category           Freq           Term          Total  loglift  logprob
term                                                                        
1367  Default   96436.000000             et   96436.000000  30.0000  30.0000
335   Default   97756.000000             al   97756.000000  29.0000  29.0000
675   Default  219324.000000          cells  219324.000000  28.0000  28.0000
959   Default   46864.000000            cov   46864.000000  27.0000  27.0000
3278  Default   40606.000000           sars   40606.000000  26.0000  26.0000
1938  Default   59260.000000      influenza   59260.0000